# Machine Learning Trading Bot

In this project, I’ll assume the role of a financial advisor at one of the top five financial advisory firms in the world. My firm constantly competes with the other major firms to manage and automatically trade assets in a highly dynamic environment. In recent years, My firm has heavily profited by using computer algorithms that can buy and sell faster than human traders.

The speed of these transactions gave my firm a competitive advantage early on. But, people still need to specifically program these systems, which limits their ability to adapt to new data. I'm thus planning to improve the existing algorithmic trading systems and maintain the firm’s competitive advantage in the market. To do so, I’ll enhance the existing trading signals with machine learning algorithms that can adapt to new data.

## Instructions:

By using the starter code file I'll complete the steps that the instructions outline. The steps for this Challenge are divided into the following sections:

* Establish a Baseline Performance

* Tune the Baseline Trading Algorithm

* Evaluate a New Machine Learning Classifier

* Create an Evaluation Report

#### Establish a Baseline Performance

In this section, I’ll run the provided starter code to establish a baseline performance for the trading algorithm. To do so, I'll complete the following steps.

Open the Jupyter notebook. Restart the kernel, run the provided cells that correspond with the first three steps, and then proceed to step four. 

1. Import the OHLCV dataset into a Pandas DataFrame.

2. Generate trading signals using short- and long-window SMA values. 

3. Split the data into training and testing datasets.

4. Use the `SVC` classifier model from SKLearn's support vector machine (SVM) learning method to fit the training data and make predictions based on the testing data. Review the predictions.

5. Review the classification report associated with the `SVC` model predictions. 

6. Create a predictions DataFrame that contains columns for “Predicted” values, “Actual Returns”, and “Strategy Returns”.

7. Create a cumulative return plot that shows the actual returns vs. the strategy returns. Save a PNG image of this plot. This will serve as a baseline against which to compare the effects of tuning the trading algorithm.

8. Write your conclusions about the performance of the baseline trading algorithm in the `README.md` file that’s associated with your GitHub repository. Support your findings by using the PNG image that you saved in the previous step.

#### Tune the Baseline Trading Algorithm

In this section, I’ll tune, or adjust, the model’s input features to find the parameters that result in the best trading outcomes. (I’ll choose the best by comparing the cumulative products of the strategy returns.) To do so, I'll complete the following steps:

1. Tune the training algorithm by adjusting the size of the training dataset. To do so, I'll slice the data into different periods. Rerun the notebook with the updated parameters, and record the results in the `README.md` file. Answer the following question: What impact resulted from increasing or decreasing the training window?

> **Hint** To adjust the size of the training dataset, I will use a different `DateOffset` value&mdash;for example, six months. Be aware that changing the size of the training dataset also affects the size of the testing dataset.

2. Tune the trading algorithm by adjusting the SMA input features. Adjust one or both of the windows for the algorithm. Rerun the notebook with the updated parameters, and record the results in your `README.md` file. Answer the following question: What impact resulted from increasing or decreasing either or both of the SMA windows?

3. Choose the set of parameters that best improved the trading algorithm returns. Save a PNG image of the cumulative product of the actual returns vs. the strategy returns, and document your conclusion in your `README.md` file.

#### Evaluate a New Machine Learning Classifier

In this section, I’ll use the original parameters that the starter code provided. But, you’ll apply them to the performance of a second machine learning model. To do so, complete the following steps:

1. Import a new classifier, such as `AdaBoost`, `DecisionTreeClassifier`, or `LogisticRegression`. (For the full list of classifiers, refer to the [Supervised learning page](https://scikit-learn.org/stable/supervised_learning.html) in the scikit-learn documentation.)

2. Using the original training data as the baseline model, fit another model with the new classifier.

3. Backtest the new model to evaluate its performance. Save a PNG image of the cumulative product of the actual returns vs. the strategy returns for this updated trading algorithm, and write your conclusions in your `README.md` file. Answer the following questions: Did this new model perform better or worse than the provided baseline model? Did this new model perform better or worse than your tuned trading algorithm?

#### Create an Evaluation Report

In the previous sections, I updated the`README.md` file with my  conclusions. To accomplish this section, I'll add a summary evaluation report at the end of the `README.md` file. For this report, I'll express my final conclusions and analysis. I'll support my findings by using the PNG images that I created.


In [49]:
# Imports
import pandas as pd
import numpy as np
from pathlib import Path
import hvplot.pandas
import matplotlib.pyplot as plt
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from pandas.tseries.offsets import DateOffset
from sklearn.metrics import classification_report

---

## Establish a Baseline Performance

In this section, you’ll run the provided starter code to establish a baseline performance for the trading algorithm. To do so, complete the following steps.

Open the Jupyter notebook. Restart the kernel, run the provided cells that correspond with the first three steps, and then proceed to step four. 


### Step 1: Import the OHLCV dataset into a Pandas DataFrame.

In [50]:
# Import the OHLCV dataset into a Pandas Dataframe
ohlcv_df = pd.read_csv(
    Path("./Resources/emerging_markets_ohlcv.csv"), 
    index_col='date', 
    infer_datetime_format=True, 
    parse_dates=True
)

# Review the DataFrame
ohlcv_df.head()

open   high    low  close  volume
date                                                   
2015-01-21 09:30:00  23.83  23.83  23.83  23.83     100
2015-01-21 11:00:00  23.98  23.98  23.98  23.98     100
2015-01-22 15:00:00  24.42  24.42  24.42  24.42     100
2015-01-22 15:15:00  24.42  24.44  24.42  24.44     200
2015-01-22 15:30:00  24.46  24.46  24.46  24.46     200

In [51]:
# Filter the date index and close columns
signals_df = ohlcv_df.loc[:, ["close"]]

# Use the pct_change function to generate  returns from close prices
signals_df["Actual Returns"] = signals_df["close"].pct_change()

# Drop all NaN values from the DataFrame
signals_df = signals_df.dropna()

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns
date                                      
2015-01-21 11:00:00  23.98        0.006295
2015-01-22 15:00:00  24.42        0.018349
2015-01-22 15:15:00  24.44        0.000819
2015-01-22 15:30:00  24.46        0.000818
2015-01-26 12:30:00  24.33       -0.005315

close  Actual Returns
date                                      
2021-01-22 09:30:00  33.27       -0.006866
2021-01-22 11:30:00  33.35        0.002405
2021-01-22 13:45:00  33.42        0.002099
2021-01-22 14:30:00  33.47        0.001496
2021-01-22 15:45:00  33.44       -0.000896

## Step 2: Generate trading signals using short- and long-window SMA values. 

In [52]:
# Set the short window and long window
short_window = 4
long_window = 100

# Generate the fast and slow simple moving averages (4 and 100 days, respectively)
signals_df['SMA_Fast'] = signals_df['close'].rolling(window=short_window).mean()
signals_df['SMA_Slow'] = signals_df['close'].rolling(window=long_window).mean()

signals_df = signals_df.dropna()

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns  SMA_Fast  SMA_Slow
date                                                          
2015-04-02 14:45:00  24.92        0.000000   24.9175   24.3214
2015-04-02 15:00:00  24.92        0.000000   24.9200   24.3308
2015-04-02 15:15:00  24.94        0.000803   24.9250   24.3360
2015-04-02 15:30:00  24.95        0.000401   24.9325   24.3411
2015-04-02 15:45:00  24.98        0.001202   24.9475   24.3463

close  Actual Returns  SMA_Fast  SMA_Slow
date                                                          
2021-01-22 09:30:00  33.27       -0.006866   33.2025  30.40215
2021-01-22 11:30:00  33.35        0.002405   33.2725  30.44445
2021-01-22 13:45:00  33.42        0.002099   33.3850  30.48745
2021-01-22 14:30:00  33.47        0.001496   33.3775  30.53085
2021-01-22 15:45:00  33.44       -0.000896   33.4200  30.57495

In [53]:
# Initialize the new Signal column
signals_df['Signal'] = 0.0

# When Actual Returns are greater than or equal to 0, generate signal to buy stock long
signals_df.loc[(signals_df['Actual Returns'] >= 0), 'Signal'] = 1

# When Actual Returns are less than 0, generate signal to sell stock short
signals_df.loc[(signals_df['Actual Returns'] < 0), 'Signal'] = -1

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns  SMA_Fast  SMA_Slow  Signal
date                                                                  
2015-04-02 14:45:00  24.92        0.000000   24.9175   24.3214     1.0
2015-04-02 15:00:00  24.92        0.000000   24.9200   24.3308     1.0
2015-04-02 15:15:00  24.94        0.000803   24.9250   24.3360     1.0
2015-04-02 15:30:00  24.95        0.000401   24.9325   24.3411     1.0
2015-04-02 15:45:00  24.98        0.001202   24.9475   24.3463     1.0

close  Actual Returns  SMA_Fast  SMA_Slow  Signal
date                                                                  
2021-01-22 09:30:00  33.27       -0.006866   33.2025  30.40215    -1.0
2021-01-22 11:30:00  33.35        0.002405   33.2725  30.44445     1.0
2021-01-22 13:45:00  33.42        0.002099   33.3850  30.48745     1.0
2021-01-22 14:30:00  33.47        0.001496   33.3775  30.53085     1.0
2021-01-22 15:45:00  33.44       -0.000896   33.4200  30.57495    -1.0

In [54]:
signals_df['Signal'].value_counts()

 1.0    2368
-1.0    1855
Name: Signal, dtype: int64

In [55]:
# Calculate the strategy returns and add them to the signals_df DataFrame
signals_df['Strategy Returns'] = signals_df['Actual Returns'] * signals_df['Signal'].shift()

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns  SMA_Fast  SMA_Slow  Signal  \
date                                                                     
2015-04-02 14:45:00  24.92        0.000000   24.9175   24.3214     1.0   
2015-04-02 15:00:00  24.92        0.000000   24.9200   24.3308     1.0   
2015-04-02 15:15:00  24.94        0.000803   24.9250   24.3360     1.0   
2015-04-02 15:30:00  24.95        0.000401   24.9325   24.3411     1.0   
2015-04-02 15:45:00  24.98        0.001202   24.9475   24.3463     1.0   

                     Strategy Returns  
date                                   
2015-04-02 14:45:00               NaN  
2015-04-02 15:00:00          0.000000  
2015-04-02 15:15:00          0.000803  
2015-04-02 15:30:00          0.000401  
2015-04-02 15:45:00          0.001202

close  Actual Returns  SMA_Fast  SMA_Slow  Signal  \
date                                                                     
2021-01-22 09:30:00  33.27       -0.006866   33.2025  30.40215    -1.0   
2021-01-22 11:30:00  33.35        0.002405   33.2725  30.44445     1.0   
2021-01-22 13:45:00  33.42        0.002099   33.3850  30.48745     1.0   
2021-01-22 14:30:00  33.47        0.001496   33.3775  30.53085     1.0   
2021-01-22 15:45:00  33.44       -0.000896   33.4200  30.57495    -1.0   

                     Strategy Returns  
date                                   
2021-01-22 09:30:00         -0.006866  
2021-01-22 11:30:00         -0.002405  
2021-01-22 13:45:00          0.002099  
2021-01-22 14:30:00          0.001496  
2021-01-22 15:45:00         -0.000896

In [56]:
# Plot Strategy Returns to examine performance
(1 + signals_df['Strategy Returns']).cumprod().hvplot()

:Curve   [date]   (Strategy Returns)

### Step 3: Split the data into training and testing datasets.

In [57]:
# Assign a copy of the sma_fast and sma_slow columns to a features DataFrame called X
X = signals_df[['SMA_Fast', 'SMA_Slow']].shift().dropna()

# Review the DataFrame
X.head()

SMA_Fast  SMA_Slow
date                                   
2015-04-02 15:00:00   24.9175   24.3214
2015-04-02 15:15:00   24.9200   24.3308
2015-04-02 15:30:00   24.9250   24.3360
2015-04-02 15:45:00   24.9325   24.3411
2015-04-06 09:30:00   24.9475   24.3463

In [58]:
# Create the target set selecting the Signal column and assiging it to y
y = signals_df['Signal']

# Review the value counts
y.value_counts()

 1.0    2368
-1.0    1855
Name: Signal, dtype: int64

In [59]:
# Select the start of the training period
training_begin = X.index.min()

# Display the training begin date
print(training_begin)

2015-04-02 15:00:00


In [60]:
# Select the ending period for the training data with an offset of 3 months
training_end = X.index.min() + DateOffset(months=3)

# Display the training end date
print(training_end)

2015-07-02 15:00:00


In [61]:
# Generate the X_train and y_train DataFrames
X_train = X.loc[training_begin:training_end]
y_train = y.loc[training_begin:training_end]

# Review the X_train DataFrame
X_train.head()

SMA_Fast  SMA_Slow
date                                   
2015-04-02 15:00:00   24.9175   24.3214
2015-04-02 15:15:00   24.9200   24.3308
2015-04-02 15:30:00   24.9250   24.3360
2015-04-02 15:45:00   24.9325   24.3411
2015-04-06 09:30:00   24.9475   24.3463

In [62]:
# Generate the X_test and y_test DataFrames
X_test = X.loc[training_end+DateOffset(hours=1):]
y_test = y.loc[training_end+DateOffset(hours=1):]

# Review the X_test DataFrame
X_train.head()

SMA_Fast  SMA_Slow
date                                   
2015-04-02 15:00:00   24.9175   24.3214
2015-04-02 15:15:00   24.9200   24.3308
2015-04-02 15:30:00   24.9250   24.3360
2015-04-02 15:45:00   24.9325   24.3411
2015-04-06 09:30:00   24.9475   24.3463

In [63]:
# Scale the features DataFrames

# Create a StandardScaler instance
scaler = StandardScaler()

# Apply the scaler model to fit the X-train data
X_scaler = scaler.fit(X_train)

# Transform the X_train and X_test DataFrames using the X_scaler
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

### Step 4: Use the `SVC` classifier model from SKLearn's support vector machine (SVM) learning method to fit the training data and make predictions based on the testing data. Review the predictions.

In [64]:
# From SVM, instantiate SVC classifier model instance
svm_model = svm.SVC()
 
# Fit the model to the data using the training data
svm_model = svm_model.fit(X_train_scaled, y_train)
 
# Use the testing data to make the model predictions
svm_pred = svm_model.predict(X_test_scaled)

# Review the model's predicted values
svm_pred[:10]


array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])

### Step 5: Review the classification report associated with the `SVC` model predictions. 

In [65]:
# Use a classification report to evaluate the model using the predictions and testing data
svm_testing_report = classification_report(y_test,svm_pred)


# Print the classification report
print("SVC Classification Report")
print("-------------------------")
print(svm_testing_report)


SVC Classification Report
-------------------------
              precision    recall  f1-score   support

        -1.0       0.43      0.04      0.07      1804
         1.0       0.56      0.96      0.71      2288

    accuracy                           0.55      4092
   macro avg       0.49      0.50      0.39      4092
weighted avg       0.50      0.55      0.43      4092



### Step 6: Create a predictions DataFrame that contains columns for “Predicted” values, “Actual Returns”, and “Strategy Returns”.

In [66]:
# Create a new empty predictions DataFrame.

# Create a predictions DataFrame
predictions_df = pd.DataFrame(index = X_test.index)

# Add the SVM model predictions to the DataFrame
predictions_df['Predicted'] = svm_pred

# Add the actual returns to the DataFrame
predictions_df['Actual Returns'] = signals_df['Actual Returns'].dropna()

# Add the strategy returns to the DataFrame
predictions_df['Strategy Returns'] = predictions_df['Actual Returns'] * predictions_df['Predicted']

# Review the DataFrame
display(predictions_df.head())
display(predictions_df.tail())

Predicted  Actual Returns  Strategy Returns
date                                                            
2015-07-06 10:00:00        1.0       -0.025715         -0.025715
2015-07-06 10:45:00        1.0        0.007237          0.007237
2015-07-06 14:15:00        1.0       -0.009721         -0.009721
2015-07-06 14:30:00        1.0       -0.003841         -0.003841
2015-07-07 11:30:00        1.0       -0.018423         -0.018423

Predicted  Actual Returns  Strategy Returns
date                                                            
2021-01-22 09:30:00        1.0       -0.006866         -0.006866
2021-01-22 11:30:00        1.0        0.002405          0.002405
2021-01-22 13:45:00        1.0        0.002099          0.002099
2021-01-22 14:30:00        1.0        0.001496          0.001496
2021-01-22 15:45:00        1.0       -0.000896         -0.000896

### Step 7: Create a cumulative return plot that shows the actual returns vs. the strategy returns. Save a PNG image of this plot. This will serve as a baseline against which to compare the effects of tuning the trading algorithm.

In [67]:
# Plot the actual returns versus the strategy returns
svc_plot=(1 + predictions_df[["Actual Returns", "Strategy Returns"]]).cumprod().hvplot(title="Actual Return vs Strategy Returns - SVC")
svc_plot

:NdOverlay   [Variable]
   :Curve   [date]   (value)

---

## Tune the Baseline Trading Algorithm

## Step 6: Use an Alternative ML Model and Evaluate Strategy Returns

In this section, you’ll tune, or adjust, the model’s input features to find the parameters that result in the best trading outcomes. You’ll choose the best by comparing the cumulative products of the strategy returns.

### Step 1: Tune the training algorithm by adjusting the size of the training dataset. 

To do so, slice your data into different periods. Rerun the notebook with the updated parameters, and record the results in your `README.md` file. 

Answer the following question: What impact resulted from increasing or decreasing the training window?

In [68]:
# Select the start of the training period
training_begin_1 = X.index.min()

# Display the training begin date
print(training_begin_1)

2015-04-02 15:00:00


In [69]:
# Select the ending period for the training data with an offset of 6 months
training_end_1 = X.index.min() + DateOffset(months=6)

# Display the training end date
print(training_end_1)

2015-10-02 15:00:00


In [70]:
# Generate the X_train and y_train DataFrames
X_train_1 = X.loc[training_begin_1:training_end_1]
y_train_1 = y.loc[training_begin_1:training_end_1]

# Review the X_train DataFrame
X_train_1.head()

SMA_Fast  SMA_Slow
date                                   
2015-04-02 15:00:00   24.9175   24.3214
2015-04-02 15:15:00   24.9200   24.3308
2015-04-02 15:30:00   24.9250   24.3360
2015-04-02 15:45:00   24.9325   24.3411
2015-04-06 09:30:00   24.9475   24.3463

In [71]:
# Generate the X_test and y_test DataFrames
X_test_1 = X.loc[training_end_1+DateOffset(hours=1):]
y_test_1 = y.loc[training_end_1+DateOffset(hours=1):]

# Review the X_test DataFrame
X_train_1.head()

SMA_Fast  SMA_Slow
date                                   
2015-04-02 15:00:00   24.9175   24.3214
2015-04-02 15:15:00   24.9200   24.3308
2015-04-02 15:30:00   24.9250   24.3360
2015-04-02 15:45:00   24.9325   24.3411
2015-04-06 09:30:00   24.9475   24.3463

In [72]:
# Scale the features DataFrames

# Create a StandardScaler instance
scaler = StandardScaler()

# Apply the scaler model to fit the X-train data
X_scaler_1 = scaler.fit(X_train_1)

# Transform the X_train and X_test DataFrames using the X_scaler
X_train_scaled_1 = X_scaler_1.transform(X_train_1)
X_test_scaled_1 = X_scaler_1.transform(X_test_1)

In [73]:
# From SVM, instantiate SVC classifier model instance
svm_model_1 = svm.SVC()
 
# Fit the model to the data using the training data
svm_model_1 = svm_model_1.fit(X_train_scaled_1, y_train_1)
 
# Use the testing data to make the model predictions
svm_pred_1 = svm_model_1.predict(X_test_scaled_1)

# Review the model's predicted values
svm_pred_1[:10]

array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])

In [74]:
# Use a classification report to evaluate the model using the predictions and testing data
svm_testing_report_1 = classification_report(y_test_1,svm_pred_1)


# Print the classification report
print("SVC Classification Report with six months offset")
print("------------------------------------------------")
print(svm_testing_report_1)

SVC Classification Report with six months offset
------------------------------------------------
              precision    recall  f1-score   support

        -1.0       0.44      0.02      0.04      1732
         1.0       0.56      0.98      0.71      2211

    accuracy                           0.56      3943
   macro avg       0.50      0.50      0.38      3943
weighted avg       0.51      0.56      0.42      3943



In [75]:
# Create a new empty predictions DataFrame.

# Create a predictions DataFrame
predictions_df_1 = pd.DataFrame(index = X_test_1.index)

# Add the SVM model predictions to the DataFrame
predictions_df_1['Predicted'] = svm_pred_1

# Add the actual returns to the DataFrame
predictions_df_1['Actual Returns'] = signals_df['Actual Returns']

# Add the strategy returns to the DataFrame
predictions_df_1['Strategy Returns'] = predictions_df_1['Actual Returns'] * predictions_df_1['Predicted']

# Review the DataFrame
display(predictions_df_1.head())
display(predictions_df_1.tail())

Predicted  Actual Returns  Strategy Returns
date                                                            
2015-10-05 09:45:00        1.0        0.013532          0.013532
2015-10-05 11:30:00        1.0        0.002302          0.002302
2015-10-05 13:15:00        1.0       -0.000919         -0.000919
2015-10-05 14:30:00        1.0        0.000920          0.000920
2015-10-05 14:45:00        1.0        0.002756          0.002756

Predicted  Actual Returns  Strategy Returns
date                                                            
2021-01-22 09:30:00        1.0       -0.006866         -0.006866
2021-01-22 11:30:00        1.0        0.002405          0.002405
2021-01-22 13:45:00        1.0        0.002099          0.002099
2021-01-22 14:30:00        1.0        0.001496          0.001496
2021-01-22 15:45:00        1.0       -0.000896         -0.000896

In [76]:
# Plot the actual returns versus the strategy returns
svc_plot_1=(1 + predictions_df_1[["Actual Returns", "Strategy Returns"]]).cumprod().hvplot(title="Actual Return vs Strategy Returns with Six months OffSet - SVC_1")
svc_plot_1

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [77]:
# Compare the original model with the tuned model 
svc_plot + svc_plot_1


:Layout
   .NdOverlay.I  :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .NdOverlay.II :NdOverlay   [Variable]
      :Curve   [date]   (value)

### Q:What impact resulted from increasing or decreasing the training window?
**Answer** By increasing the training window from 3 months to 6 months the model has improved.The return generetd by the tuned model has increased (1.52 vs 1.843).

### Step 2: Tune the trading algorithm by adjusting the SMA input features. 

Adjust one or both of the windows for the algorithm. Rerun the notebook with the updated parameters, and record the results in your `README.md` file. 

Answer the following question: What impact resulted from increasing or decreasing either or both of the SMA windows?

### Generate new trading signals using short- and long-window SMA values.

In [78]:

# Filter the date index and close columns
signals_df = ohlcv_df.loc[:, ["close"]]

# Use the pct_change function to generate  returns from close prices
signals_df["Actual Returns"] = signals_df["close"].pct_change()

# Drop all NaN values from the DataFrame
signals_df = signals_df.dropna()

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns
date                                      
2015-01-21 11:00:00  23.98        0.006295
2015-01-22 15:00:00  24.42        0.018349
2015-01-22 15:15:00  24.44        0.000819
2015-01-22 15:30:00  24.46        0.000818
2015-01-26 12:30:00  24.33       -0.005315

close  Actual Returns
date                                      
2021-01-22 09:30:00  33.27       -0.006866
2021-01-22 11:30:00  33.35        0.002405
2021-01-22 13:45:00  33.42        0.002099
2021-01-22 14:30:00  33.47        0.001496
2021-01-22 15:45:00  33.44       -0.000896

In [79]:
# Set the short window and long window
short_window = 5
long_window = 120

# Generate the fast and slow simple moving averages (5 and 120 days, respectively)
signals_df['SMA_Fast'] = signals_df['close'].rolling(window=short_window).mean()
signals_df['SMA_Slow'] = signals_df['close'].rolling(window=long_window).mean()

signals_df = signals_df.dropna()

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns  SMA_Fast   SMA_Slow
date                                                           
2015-04-09 12:15:00  25.78        0.003894    25.720  24.488250
2015-04-09 12:45:00  25.77       -0.000388    25.726  24.503167
2015-04-09 13:15:00  25.79        0.000776    25.744  24.514583
2015-04-09 13:45:00  25.80        0.000388    25.764  24.525917
2015-04-09 14:00:00  25.80        0.000000    25.788  24.537083

close  Actual Returns  SMA_Fast   SMA_Slow
date                                                           
2021-01-22 09:30:00  33.27       -0.006866    33.192  30.054708
2021-01-22 11:30:00  33.35        0.002405    33.232  30.104125
2021-01-22 13:45:00  33.42        0.002099    33.302  30.153958
2021-01-22 14:30:00  33.47        0.001496    33.402  30.204458
2021-01-22 15:45:00  33.44       -0.000896    33.390  30.256792

In [80]:
# Initialize the new Signal column
signals_df['Signal'] = 0.0

# When Actual Returns are greater than or equal to 0, generate signal to buy stock long
signals_df.loc[(signals_df['Actual Returns'] >= 0), 'Signal'] = 1

# When Actual Returns are less than 0, generate signal to sell stock short
signals_df.loc[(signals_df['Actual Returns'] < 0), 'Signal'] = -1

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns  SMA_Fast   SMA_Slow  Signal
date                                                                   
2015-04-09 12:15:00  25.78        0.003894    25.720  24.488250     1.0
2015-04-09 12:45:00  25.77       -0.000388    25.726  24.503167    -1.0
2015-04-09 13:15:00  25.79        0.000776    25.744  24.514583     1.0
2015-04-09 13:45:00  25.80        0.000388    25.764  24.525917     1.0
2015-04-09 14:00:00  25.80        0.000000    25.788  24.537083     1.0

close  Actual Returns  SMA_Fast   SMA_Slow  Signal
date                                                                   
2021-01-22 09:30:00  33.27       -0.006866    33.192  30.054708    -1.0
2021-01-22 11:30:00  33.35        0.002405    33.232  30.104125     1.0
2021-01-22 13:45:00  33.42        0.002099    33.302  30.153958     1.0
2021-01-22 14:30:00  33.47        0.001496    33.402  30.204458     1.0
2021-01-22 15:45:00  33.44       -0.000896    33.390  30.256792    -1.0

In [81]:
signals_df['Signal'].value_counts()

 1.0    2354
-1.0    1849
Name: Signal, dtype: int64

In [82]:
# Calculate the strategy returns and add them to the signals_df DataFrame
signals_df['Strategy Returns'] = signals_df['Actual Returns'] * signals_df['Signal'].shift()

# Review the DataFrame
display(signals_df.head())
display(signals_df.tail())

close  Actual Returns  SMA_Fast   SMA_Slow  Signal  \
date                                                                      
2015-04-09 12:15:00  25.78        0.003894    25.720  24.488250     1.0   
2015-04-09 12:45:00  25.77       -0.000388    25.726  24.503167    -1.0   
2015-04-09 13:15:00  25.79        0.000776    25.744  24.514583     1.0   
2015-04-09 13:45:00  25.80        0.000388    25.764  24.525917     1.0   
2015-04-09 14:00:00  25.80        0.000000    25.788  24.537083     1.0   

                     Strategy Returns  
date                                   
2015-04-09 12:15:00               NaN  
2015-04-09 12:45:00         -0.000388  
2015-04-09 13:15:00         -0.000776  
2015-04-09 13:45:00          0.000388  
2015-04-09 14:00:00          0.000000

close  Actual Returns  SMA_Fast   SMA_Slow  Signal  \
date                                                                      
2021-01-22 09:30:00  33.27       -0.006866    33.192  30.054708    -1.0   
2021-01-22 11:30:00  33.35        0.002405    33.232  30.104125     1.0   
2021-01-22 13:45:00  33.42        0.002099    33.302  30.153958     1.0   
2021-01-22 14:30:00  33.47        0.001496    33.402  30.204458     1.0   
2021-01-22 15:45:00  33.44       -0.000896    33.390  30.256792    -1.0   

                     Strategy Returns  
date                                   
2021-01-22 09:30:00         -0.006866  
2021-01-22 11:30:00         -0.002405  
2021-01-22 13:45:00          0.002099  
2021-01-22 14:30:00          0.001496  
2021-01-22 15:45:00         -0.000896

In [83]:
# Plot Strategy Returns to examine performance
(1 + signals_df['Strategy Returns']).cumprod().hvplot()

:Curve   [date]   (Strategy Returns)

In [84]:
# Assign a copy of the sma_fast and sma_slow columns to a features DataFrame called X
X = signals_df[['SMA_Fast', 'SMA_Slow']].shift().dropna()

# Review the DataFrame
X.head()

SMA_Fast   SMA_Slow
date                                    
2015-04-09 12:45:00    25.720  24.488250
2015-04-09 13:15:00    25.726  24.503167
2015-04-09 13:45:00    25.744  24.514583
2015-04-09 14:00:00    25.764  24.525917
2015-04-09 14:30:00    25.788  24.537083

In [85]:
# Create the target set selecting the Signal column and assiging it to y
y = signals_df['Signal']

# Review the value counts
y.value_counts()

 1.0    2354
-1.0    1849
Name: Signal, dtype: int64

In [86]:
# Select the start of the training period
training_begin_2 = X.index.min()

# Display the training begin date
print(training_begin_2)

2015-04-09 12:45:00


In [87]:
# Select the ending period for the training data with an offset of 6 months
training_end_2 = X.index.min() + DateOffset(months=6)

# Display the training end date
print(training_end_2)

2015-10-09 12:45:00


In [88]:
# Generate the X_train and y_train DataFrames
X_train_2 = X.loc[training_begin_2:training_end_2]
y_train_2 = y.loc[training_begin_2:training_end_2]

# Review the X_train DataFrame
X_train_2.head()

SMA_Fast   SMA_Slow
date                                    
2015-04-09 12:45:00    25.720  24.488250
2015-04-09 13:15:00    25.726  24.503167
2015-04-09 13:45:00    25.744  24.514583
2015-04-09 14:00:00    25.764  24.525917
2015-04-09 14:30:00    25.788  24.537083

In [89]:
# Generate the X_test and y_test DataFrames
X_test_2 = X.loc[training_end_2+DateOffset(hours=1):]
y_test_2 = y.loc[training_end_2+DateOffset(hours=1):]

# Review the X_test DataFrame
X_train_2.head()

SMA_Fast   SMA_Slow
date                                    
2015-04-09 12:45:00    25.720  24.488250
2015-04-09 13:15:00    25.726  24.503167
2015-04-09 13:45:00    25.744  24.514583
2015-04-09 14:00:00    25.764  24.525917
2015-04-09 14:30:00    25.788  24.537083

In [90]:
# Scale the features DataFrames

# Create a StandardScaler instance
scaler = StandardScaler()

# Apply the scaler model to fit the X-train data
X_scaler_2 = scaler.fit(X_train_2)

# Transform the X_train and X_test DataFrames using the X_scaler
X_train_scaled_2 = X_scaler_2.transform(X_train_2)
X_test_scaled_2 = X_scaler_2.transform(X_test_2)

### Use the SVC classifier model from SKLearn's support vector machine (SVM) learning method to fit the training data and make predictions based on the testing data. Review the predictions.

In [91]:
# From SVM, instantiate SVC classifier model instance
svm_model_2 = svm.SVC()
 
# Fit the model to the data using the training data
svm_model_2 = svm_model_2.fit(X_train_scaled_2, y_train_2)
 
# Use the testing data to make the model predictions
svm_pred_2 = svm_model_2.predict(X_test_scaled_2)

# Review the model's predicted values
svm_pred_2[:10]

array([1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])

### Review the classification report associated with the `SVC` model predictions.

In [92]:
# Use a classification report to evaluate the model using the predictions and testing data
svm_testing_report_2 = classification_report(y_test_2,svm_pred_2)


# Print the classification report
print("SVC Classification Report SMA(5,120)")
print("----------------------------------------------------------------")
print(svm_testing_report_2)

SVC Classification Report SMA(5,120)
----------------------------------------------------------------
              precision    recall  f1-score   support

        -1.0       0.48      0.01      0.03      1722
         1.0       0.56      0.99      0.72      2196

    accuracy                           0.56      3918
   macro avg       0.52      0.50      0.37      3918
weighted avg       0.53      0.56      0.41      3918



### Create a predictions DataFrame that contains columns for “Predicted” values, “Actual Returns”, and “Strategy Returns”.

In [93]:
# Create a new empty predictions DataFrame.

# Create a predictions DataFrame
predictions_df_2 = pd.DataFrame(index = X_test_2.index)

# Add the SVM model predictions to the DataFrame
predictions_df_2['Predicted'] = svm_pred_2

# Add the actual returns to the DataFrame
predictions_df_2['Actual Returns'] = signals_df['Actual Returns'].dropna()

# Add the strategy returns to the DataFrame
predictions_df_2['Strategy Returns'] = predictions_df_2['Actual Returns'] * predictions_df_2['Predicted']

# Review the DataFrame
display(predictions_df_2.head())
display(predictions_df_2.tail())

Predicted  Actual Returns  Strategy Returns
date                                                            
2015-10-12 15:30:00        1.0       -0.006667         -0.006667
2015-10-13 13:30:00        1.0       -0.007159         -0.007159
2015-10-13 13:45:00        1.0        0.001352          0.001352
2015-10-13 15:15:00        1.0       -0.003150         -0.003150
2015-10-13 15:45:00        1.0       -0.000451         -0.000451

Predicted  Actual Returns  Strategy Returns
date                                                            
2021-01-22 09:30:00        1.0       -0.006866         -0.006866
2021-01-22 11:30:00        1.0        0.002405          0.002405
2021-01-22 13:45:00        1.0        0.002099          0.002099
2021-01-22 14:30:00        1.0        0.001496          0.001496
2021-01-22 15:45:00        1.0       -0.000896         -0.000896

### Create a cumulative return plot that shows the actual returns vs. the strategy returns. Save a PNG image of this plot. This will serve as a baseline against which to compare the effects of tuning the trading algorithm.

In [94]:
# Plot the actual returns versus the strategy returns
svc_plot_2=(1 + predictions_df_2[["Actual Returns", "Strategy Returns"]]).cumprod().hvplot(title="Actual Return vs Strategy Returns with SMA(5 days,120 days)- SVC_2")
svc_plot_2

:NdOverlay   [Variable]
   :Curve   [date]   (value)

### Answer the following question: What impact resulted from increasing or decreasing either or both of the SMA windows?

**Answer:** By increasing the SMA windows for short term from 4 to 5 days and for long from 100 to 120 days with the six months training window model's performance has declined from 1.845 to 1.658.

### Step 3: Choose the set of parameters that best improved the trading algorithm returns. 

Save a PNG image of the cumulative product of the actual returns vs. the strategy returns, and document your conclusion in your `README.md` file.

---

## Evaluate a New Machine Learning Classifier

In this section, you’ll use the original parameters that the starter code provided. But, you’ll apply them to the performance of a second machine learning model. 

### Step 1:  Import a new classifier, such as `AdaBoost`, `DecisionTreeClassifier`, or `LogisticRegression`. (For the full list of classifiers, refer to the [Supervised learning page](https://scikit-learn.org/stable/supervised_learning.html) in the scikit-learn documentation.)

In [95]:
# Import a new classifier from SKLearn
from sklearn import tree
#from sklearn.linear_model import LogisticRegression
# Initiate the model instance
#lr_model = LogisticRegression()
dtc_model = tree.DecisionTreeClassifier()

### Step 2: Using the original training data as the baseline model, fit another model with the new classifier.

In [96]:
# Fit the model using the training data
dtc_model = dtc_model.fit(X_train_scaled, y_train)

# Use the testing dataset to generate the predictions for the new model
dtc_pred = dtc_model.predict(X_test_scaled)

# Review the model's predicted values
dtc_pred[:10]


array([ 1., -1., -1., -1., -1., -1., -1., -1., -1., -1.])

### Step 3: Backtest the new model to evaluate its performance. 

Save a PNG image of the cumulative product of the actual returns vs. the strategy returns for this updated trading algorithm, and write your conclusions in your `README.md` file. 

Answer the following questions: 
Did this new model perform better or worse than the provided baseline model? 
Did this new model perform better or worse than your tuned trading algorithm?

In [97]:
# Use a classification report to evaluate the model using the predictions and testing data
dtc_testing_report = classification_report(y_test, dtc_pred)


# Print the classification report
print("DTC Classification Report ")
print("--------------------------")
print(dtc_testing_report)


DTC Classification Report 
--------------------------
              precision    recall  f1-score   support

        -1.0       0.44      0.91      0.59      1804
         1.0       0.56      0.09      0.15      2288

    accuracy                           0.45      4092
   macro avg       0.50      0.50      0.37      4092
weighted avg       0.51      0.45      0.35      4092



In [98]:
# Create a new empty predictions DataFrame.

# Create a predictions DataFrame
dtc_pred_df = pd.DataFrame(index = X_test.index)

# Add the new model predictions to the DataFrame
dtc_pred_df['Predicted'] = dtc_pred

# Add the actual returns to the DataFrame
dtc_pred_df['Actual Returns'] = signals_df['Actual Returns']


# Add the strategy returns to the DataFrame
dtc_pred_df['Strategy Returns'] = dtc_pred_df['Actual Returns'] * dtc_pred_df['Predicted']


# Review the DataFrame
display(dtc_pred_df.head())
display(dtc_pred_df.tail())


Predicted  Actual Returns  Strategy Returns
date                                                            
2015-07-06 10:00:00        1.0       -0.025715         -0.025715
2015-07-06 10:45:00       -1.0        0.007237         -0.007237
2015-07-06 14:15:00       -1.0       -0.009721          0.009721
2015-07-06 14:30:00       -1.0       -0.003841          0.003841
2015-07-07 11:30:00       -1.0       -0.018423          0.018423

Predicted  Actual Returns  Strategy Returns
date                                                            
2021-01-22 09:30:00       -1.0       -0.006866          0.006866
2021-01-22 11:30:00       -1.0        0.002405         -0.002405
2021-01-22 13:45:00       -1.0        0.002099         -0.002099
2021-01-22 14:30:00       -1.0        0.001496         -0.001496
2021-01-22 15:45:00       -1.0       -0.000896          0.000896

In [99]:
# Plot the actual returns versus the strategy returns
dtc_plot=(1 + dtc_pred_df[["Actual Returns", "Strategy Returns"]]).cumprod().hvplot(title="Actual Return vs Strategy Returns- DTC")
dtc_plot

:NdOverlay   [Variable]
   :Curve   [date]   (value)

### Answer the following questions: Did this new model perform better or worse than the provided baseline model? Did this new model perform better or worse than your tuned trading algorithm?

In [100]:
#Did this new model perform better or worse than the provided baseline model?
#Compare new model with the baseline model

print("DTC testing Report")
print(dtc_testing_report)
print("-------------------------------------------------------")
print("SVC Testing Report")
print(svm_testing_report)

DTC testing Report
              precision    recall  f1-score   support

        -1.0       0.44      0.91      0.59      1804
         1.0       0.56      0.09      0.15      2288

    accuracy                           0.45      4092
   macro avg       0.50      0.50      0.37      4092
weighted avg       0.51      0.45      0.35      4092

-------------------------------------------------------
SVC Testing Report
              precision    recall  f1-score   support

        -1.0       0.43      0.04      0.07      1804
         1.0       0.56      0.96      0.71      2288

    accuracy                           0.55      4092
   macro avg       0.49      0.50      0.39      4092
weighted avg       0.50      0.55      0.43      4092



In [101]:
svc_plot + dtc_plot

:Layout
   .NdOverlay.I  :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .NdOverlay.II :NdOverlay   [Variable]
      :Curve   [date]   (value)

In [102]:
#Did this new model perform better or worse than your tuned trading algorithm?
# compare the new model with the tuned tradind algorithm
svc_plot_1 + dtc_plot

:Layout
   .NdOverlay.I  :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .NdOverlay.II :NdOverlay   [Variable]
      :Curve   [date]   (value)

In [103]:
#Did this new model perform better or worse than your tuned trading algorithm?
svc_plot_2 + dtc_plot

:Layout
   .NdOverlay.I  :NdOverlay   [Variable]
      :Curve   [date]   (value)
   .NdOverlay.II :NdOverlay   [Variable]
      :Curve   [date]   (value)

In [104]:
# compare the classification report of all the models
print("SVC Classification Report")
print(svm_testing_report)
print("--------------------------------------------------------")
print("SVC Classification Report_1")
print(svm_testing_report_1)
print("---------------------------------------------------------")
print("SVC Classification Report_2")
print(svm_testing_report_2)
print("-------------------------------------------------------")
print("DTC Classification Report")
print(dtc_testing_report)


SVC Classification Report
              precision    recall  f1-score   support

        -1.0       0.43      0.04      0.07      1804
         1.0       0.56      0.96      0.71      2288

    accuracy                           0.55      4092
   macro avg       0.49      0.50      0.39      4092
weighted avg       0.50      0.55      0.43      4092

--------------------------------------------------------
SVC Classification Report_1
              precision    recall  f1-score   support

        -1.0       0.44      0.02      0.04      1732
         1.0       0.56      0.98      0.71      2211

    accuracy                           0.56      3943
   macro avg       0.50      0.50      0.38      3943
weighted avg       0.51      0.56      0.42      3943

---------------------------------------------------------
SVC Classification Report_2
              precision    recall  f1-score   support

        -1.0       0.48      0.01      0.03      1722
         1.0       0.56      0.99      0